## Równanie ciepła w 3D i w czasie metodą elementu skończonego

### Modyfikacja ###

Element standardowy: ostrosłup trójkątny $T$ o wierzchołkach $(0,0,0), (1,0,0), (0,1,0), (0,0,1)$
Funkcje kształtu: $$\begin{align}
\Lambda_0(x,y,z) &= 1 - x - y - z \\ \Lambda_1(x,y,z) &= x \\ \Lambda_2(x,y,z) &= y \\ \Lambda_3(x,y,z) &= z
\end{align}$$

Przekształcenia afiniczne: $$\begin{align}
\phi_e: T &\to \Omega_e \\
\vec{x} &\mapsto M_e \vec{x} + \vec{x_0}
\end{align}$$ gdzie $$M_e = \begin{pmatrix}
\uparrow & \uparrow & \uparrow \\
\vec{x_1}-\vec{x_0} & \vec{x_2}-\vec{x_0} & \vec{x_3}-\vec{x_0} \\
\downarrow & \downarrow & \downarrow
\end{pmatrix}$$
oraz $\det M^e = 6\Delta$ gdzie $\Delta$ to objętość elementu skończonego $e$.

Macierze z całkami:
$$
\begin{align}
A_{ij}^e &= \int_{\Omega_e}\xi_i(\vec{x})\xi_j(\vec{x})d\Omega \\
&= \int_T\Lambda_i(\phi_e^{-1}(\vec{y}))\Lambda_j(\phi_e^{-1}(\vec{y}))\vert\frac{\partial\phi_e}{\partial y}\vert dT \\
&= 6\Delta_e\int_{x=0}^1\int_{y=0}^{1-x}\int_{z=0}^{1-x-y}\Lambda_i(x,y)\Lambda_j(x,y)dxdydz\\
&= \frac{\Delta_e}{20} 
\begin{pmatrix}
2 & 1 & 1 & 1 \\
1 & 2 & 1 & 1 \\
1 & 1 & 2 & 1 \\
1 & 1 & 1 & 2
\end{pmatrix}\\
\\
B_{ij}^e &= \int_{\Omega_e}\nabla\xi_i(\vec{x})\cdot\nabla\xi_j(\vec{x})d\Omega \\
&= 6\Delta_e\int_T \nabla\Lambda_i\cdot \nabla\Lambda_j d\Omega \\
&= \Delta_e
\begin{pmatrix}
3 & -1 & -1 & -1\\
-1 & 1 & 0 & 0\\
-1 & 0 & 1 & 0 \\
-1 & 0 & 0 & 1
\end{pmatrix}
\end{align}
$$

In [1]:
import matplotlib.pyplot as plt
plt.style.use('dark_background')
import matplotlib.tri as tri

import numpy as np
#from  tqdm.notebook import trange
from tqdm import tqdm
#%matplotlib inline

In [2]:
class Setup:
    def __init__(self, nodes, boundary_nodes, elements, f, g, t_range = (0.0, 1.0), dt = 0.1, output_freq: int = 100):
        self.nodes = np.array(nodes)
        self.boundary_nodes = np.array(boundary_nodes)
        self.elements = np.array(elements)
        
        self.t_range = t_range
        self.t_num = round((self.t_range[1] - self.t_range[0]) / dt) + 1
        self.output_freq = output_freq
        self.T, self.dt = np.linspace(*self.t_range, self.t_num, retstep=True)
        
        self.f = f
        self.g = g

In [3]:
from numpy import loadtxt
filename = "modele/cow.1"
#filename = "modele/gear.1"
elements = loadtxt(filename+".ele", unpack=False, comments="#", skiprows=1, usecols=(1,2,3,4), dtype=int)
faces = loadtxt(filename+".face", unpack=False, comments="#", skiprows=1, usecols=(1,2,3), dtype=int)
#elements -= 1
#faces -= 1

nodes = loadtxt(filename+".node", unpack=False, comments="#", skiprows=1, usecols=(1,2,3))

"""
def find_boundary_nodes(faces, elements):
    boundary_nodes = []
    faces_dict = {}
    for i,j,k in faces:
        if (i > j): i,j=j,i
        if (j > k): j,k=k,j
        if (i > j): i,j=j,i
        f = (i,j,k)
        for e in elements:
            if set(f).issubset(set(e)):
                if f in faces_dict: faces_dict[f] += 1
                else: faces_dict[f] = 1
    
    boundary_nodes = []
    print(faces_dict)
    for key,val in faces_dict:
        if val == 1:
            [i,j,k] = list(key)
            if i not in boundary_nodes: boundary_nodes.append(i)
            if j not in boundary_nodes: boundary_nodes.append(j)
            if k not in boundary_nodes: boundary_nodes.append(j)
    return boundary_nodes
"""
#print(elements)
#for i,j,k in faces:
#    if i not in boundary_nodes: boundary_nodes.append(i)
#    if j not in boundary_nodes: boundary_nodes.append(j)
#    if k not in boundary_nodes: boundary_nodes.append(k)
#boundary_nodes = np.unique(faces.reshape((-1,1)))[0:1]
#print(boundary_nodes)

#nodes_raw = loadtxt(filename+".node", unpack=False, comments="#", skiprows=1, dtype={'names': ('id', 'x', 'y', 'z'), 'formats': ('i4', 'f4', 'f4', 'f4')})
#num = max(nodes_raw['id'])
#nodes = np.zeros((num+1,3))
#for node in nodes_raw:
#    nodes[node['id']] = [node['x'], node['y'], node['z']]
#print(num)
#print(nodes)

#elements -= 1
#faces -= 1

#print(elements)
#print(nodes)
#print(faces)

'\ndef find_boundary_nodes(faces, elements):\n    boundary_nodes = []\n    faces_dict = {}\n    for i,j,k in faces:\n        if (i > j): i,j=j,i\n        if (j > k): j,k=k,j\n        if (i > j): i,j=j,i\n        f = (i,j,k)\n        for e in elements:\n            if set(f).issubset(set(e)):\n                if f in faces_dict: faces_dict[f] += 1\n                else: faces_dict[f] = 1\n    \n    boundary_nodes = []\n    print(faces_dict)\n    for key,val in faces_dict:\n        if val == 1:\n            [i,j,k] = list(key)\n            if i not in boundary_nodes: boundary_nodes.append(i)\n            if j not in boundary_nodes: boundary_nodes.append(j)\n            if k not in boundary_nodes: boundary_nodes.append(j)\n    return boundary_nodes\n'

In [4]:

"""
from meshpy.tet import MeshInfo, build

mesh_info = MeshInfo()
mesh_info.set_points([
    (0,0,0), (2,0,0), (2,2,0), (0,2,0),
    (0,0,12), (2,0,12), (2,2,12), (0,2,12),
    ])
mesh_info.set_facets([
    [0,1,2,3],
    [4,5,6,7],
    [0,4,5,1],
    [1,5,6,2],
    [2,6,7,3],
    [3,7,4,0],
    ])
mesh = build(mesh_info)
"""


'\nfrom meshpy.tet import MeshInfo, build\n\nmesh_info = MeshInfo()\nmesh_info.set_points([\n    (0,0,0), (2,0,0), (2,2,0), (0,2,0),\n    (0,0,12), (2,0,12), (2,2,12), (0,2,12),\n    ])\nmesh_info.set_facets([\n    [0,1,2,3],\n    [4,5,6,7],\n    [0,4,5,1],\n    [1,5,6,2],\n    [2,6,7,3],\n    [3,7,4,0],\n    ])\nmesh = build(mesh_info)\n'

In [5]:
dt = 0.5
output_freq = 1
t_range = (0.0, 20.0)

F = lambda x,y,z,t: 0

# dirichlet
#G = lambda x,y,z,t: 100*t*x*y*z
#G = lambda x,y,z,t: 100*(1-t) if t < 1 else 0
#G = lambda x,y,z,t: np.sin(np.pi*t/10) if t < 10 else 0
G = lambda x,y,z,t: 1

boundary_nodes = [n for n in range(200)]
#boundary_nodes = [2]
setup = Setup(nodes, boundary_nodes, elements, F, G, t_range, dt, output_freq)

In [6]:
DIMENSION_DOMAIN = 3
NODES_PER_ELEMENT = 4


Equation indecces mapping

In [7]:
global_size = len(setup.nodes)
ID = np.arange(global_size).reshape(-1, 1)

Finite Element class

In [8]:
class FiniteElement:
    size = NODES_PER_ELEMENT
    
    def __init__(self, e, setup, rhs):
        self.setup = setup
        self.rhs = rhs
        self.eq_ids = np.zeros(FiniteElement.size)
        self.coord = np.zeros((NODES_PER_ELEMENT, DIMENSION_DOMAIN))
        self.node_ids = np.zeros(NODES_PER_ELEMENT)
        z = 0
        for j in range(NODES_PER_ELEMENT):
            J = int(setup.elements[e, j])
            self.eq_ids[j] = ID[J, 0]
            self.coord[j] = setup.nodes[J]
            self.node_ids[j] = J
            
        self.A, self.B = self.make_integrals()
        self.K, self.F = self.make_stiffness_matrix()

    def make_integrals(self):
        i = 0; j = 1; k = 2; l = 3
        x = 0; y = 1; z = 2
        
        coord = self.coord
        bj = coord[j, x] - coord[i, x]
        bk = coord[k, x] - coord[i, x]
        bl = coord[l, x] - coord[i, x]

        cj = coord[j, y] - coord[i, y]
        ck = coord[k, y] - coord[i, y]
        cl = coord[l, y] - coord[i, y]
        
        dj = coord[j, z] - coord[i, z]
        dk = coord[k, z] - coord[i, z]
        dl = coord[l, z] - coord[i, z]
        
        detM = abs(bj*(ck*dl-dk*cl) - bk*(cj*dl-cl*dj) + bl*(cj*dk-ck*dj))
        volume = detM / 6
        
        A = (volume/20) * np.array([
            [2, 1, 1, 1],
            [1, 2, 1, 1],
            [1, 1, 2, 1],
            [1, 1, 1, 2]
        ])
        
        B = volume * np.array([
            [3, -1, -1, -1],
            [-1, 1, 0, 0],
            [-1, 0, 1, 0],
            [-1, 0, 0, 1]
        ])
        return A, B

    def make_stiffness_matrix(self):
        dt = self.setup.dt
        coord = self.coord

        Ke = self.A + dt*self.B
        we = np.array([self.rhs[int(node_id)] for node_id in self.node_ids])
        Fe = self.A.dot(we)
        return Ke, Fe

In [9]:
def solve(setup, dirichlet, u, f):
    K = np.zeros((global_size, global_size))
    F = np.zeros((global_size, 1))

    rhs = u + setup.dt * f
    for e in range(len(setup.elements)):
        element = FiniteElement(e, setup, rhs)

        for i in range(FiniteElement.size):
            I = int(element.eq_ids[i])
            for j in range(FiniteElement.size):
                J = int(element.eq_ids[j])  
                # Adds element matrix K to global matrix K
                K[I, J] += element.K[i,j]
            # Adds load element vector F in F
            F[I] += element.F[i]
            
    # Dirichlet
    for node, value in dirichlet:    
        i = ID[int(node), 0]  # >_<
        F[:, 0] = F[:, 0] - value * K[:, i]
        K[i, :] = 0.0
        K[:, i] = 0.0
        K[i, i] = 1.0
        F[i] = value
        
    return np.squeeze(np.linalg.solve(K, F).reshape(len(setup.nodes), 1))

In [10]:
#%%time

u_matrix = np.zeros((len(setup.nodes), setup.t_num // setup.output_freq))

u = np.zeros(len(setup.nodes))
for node in setup.boundary_nodes:
    x,y,z = setup.nodes[node]
    value = setup.g(x,y,z,setup.T[0])
    u[node] = value

u_matrix[:,0] = u
pbar = tqdm(range(1, (setup.t_num // setup.output_freq) * setup.output_freq))
for t in pbar:
    pbar.set_description("t={:.4f}".format(setup.T[t]))

    fn = np.array([setup.f(xi, yi, zi, setup.T[t]) for (xi, yi, zi) in setup.nodes])
    dirichlet = []
    for node in setup.boundary_nodes:
        x,y,z = setup.nodes[node]
        value = setup.g(x,y,z,setup.T[t])
        dirichlet.append([node, value])
        
    u = solve(setup, dirichlet, u, fn)
    if t % setup.output_freq == 0:
        u_matrix[:, t // setup.output_freq] = u

t=20.0000: 100%|████████████████████████████████| 40/40 [00:49<00:00,  1.23s/it]


In [14]:
cmax = u_matrix.max()
cmin = u_matrix.min()

In [21]:
import plotly.graph_objects as go
#frames = []
#print(u_matrix.shape)
#print(u_matrix[:,5])
#print(len(u_matrix[0]))
x, y, z = nodes.T
frames =[dict(data=[dict(type='mesh3d', intensity=u_matrix[:,i])],
                  traces=[0],
                  name='t={0:.4f}'.format(setup.T[i])) for i in range(len(u_matrix[0]))]

i = faces[:,0]
j = faces[:,1]
k = faces[:,2]

fig_dict = {
    "data": [],
    "layout": {},
    "frames": []
}

fig_dict["data"] = [
    go.Mesh3d(
        x=x, y=y, z=z,
        colorbar_title='temperatura',
        colorscale=[[0, 'blue'], [1, 'yellow']],
        intensity=u_matrix[:,0],
        i=i, j=j, k=k, opacity=1.0,
        cmin=cmin, cmax=cmax,
    )]

fig_dict["layout"]["updatemenus"] = [
    {
        "buttons": [
            {
                "args": [None, {"frame": {"duration": 1000*dt*setup.output_freq, "redraw": True},
                                "fromcurrent": True, "transition": False}],
                "label": "Start",
                "method": "animate"
            },
            {
                "args": [[None], {"frame": {"duration": 0, "redraw": True},
                                  "mode": "immediate",
                                  "transition": {"duration": 0}}],
                "label": "Stop",
                "method": "animate"
            }
        ],
        "direction": "left",
        "pad": {"r": 10, "t": 87},
        "showactive": False,
        "type": "buttons",
        "x": 0.1,
        "xanchor": "right",
        "y": 0,
        "yanchor": "top"
    }
]
fig_dict["layout"]["autosize"] = False
fig_dict["layout"]["width"] = 1000
fig_dict["layout"]["height"] = 1000

fig_dict["frames"] = frames
fig = go.Figure(fig_dict)

for k in range(len(fig.frames)):
    fig.frames[k]['layout'].update(title_text='t={0:.4f}'.format(setup.T[k]))

fig.show()

----